In [1]:
import os
import re
import csv
import glob
import time
from collections import OrderedDict
import pandas as pd

## read male scientists (男性の科学者）articles data downloaded from PetScan (https://petscan.wmflabs.org/?psid=22389294)
### User manual (https://meta.wikimedia.org/wiki/PetScan/)
-  read download.csv (scientist by nationality|4 people|20 birth year|20 without female scientist|20)

In [2]:
df = pd.read_csv("m_scientist.csv")
df.head(20)

number         title  pageid  namespace  length         touched
0        1          手塚治虫     493        NaN  243467  20220628000314
1        2     ドナルド・クヌース    1023        NaN   33200  20220626162122
2        3    マービン・ミンスキー    1033        NaN   18950  20220514174157
3        4    ノーム・チョムスキー    1093        NaN   77897  20220616044650
4        5   エドガー・ダイクストラ    1130        NaN   29015  20211022093144
5        6  リチャード・ストールマン    1170        NaN   23845  20220212221959
6        7      シャルル・メシエ    1406        NaN    6736  20220311074733
7        8            老子    1432        NaN   58730  20220623035549
8        9          小柴昌俊    1450        NaN   21193  20220629120537
9       10          大森一樹    1965        NaN   19468  20220505014420
10      11    ジョン・マッカーシー    2345        NaN   23743  20220512153750
11      12          湯川秀樹    2592        NaN   55019  20220616052358
12      13    ゲイリー・キルドール    2781        NaN   34258  20211008153715
13      14         朝永振一郎    2909        NaN   28932  20220630004911
14      15  ジョン・フォン・ノイマン    3359        NaN   56860  20220426191946
15      16      ケン・トンプソン    3394        NaN   26071  20220215021728
16      17      デニス・リッチー    3396        NaN   24547  20220215021705
17      18   ブライアン・カーニハン    3397        NaN    5095  20211207213926
18      19     クロード・シャノン    3447        NaN   19785  20220702024341
19      20    アラン・チューリング    3449        NaN   80669  20220629211506

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24648 entries, 0 to 24647
Data columns (total 6 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   number     24648 non-null  int64  
 1   title      24648 non-null  object 
 2   pageid     24648 non-null  int64  
 3   namespace  0 non-null      float64
 4   length     24648 non-null  int64  
 5   touched    24648 non-null  int64  
dtypes: float64(1), int64(4), object(1)
memory usage: 1.1+ MB


### In Denelezh (https://denelezh.wmcloud.org/gender-gap/?project=jawiki) there should be1,659 female scientists as in 2020-09-21


In [4]:
# key: folder's name, value: create dictionartris of max IDs
# exrtract max ID values from the last article in the last file in each directory
def mapping_dir(dir_path):
    dir_list = os.listdir(dir_path)
    for _dir in dir_list:
        last_f_path = sorted(glob.glob(os.path.join(dir_path, _dir) + '\\*'))[-1]
        max_id, _, _ = format_text(sorted(get_articlelist(last_f_path))[-1])
        dir_info[_dir] = max_id
    return dir_info


In [5]:
# pade_id from csv file and dir_info created by mapping_dir
# return folder name which include page_id I'm looking for
def get_search_dir(page_id, dir_info):
    min_id = 0
    for dir_name, max_id in dir_info.items():
        search_dir = dir_name
        if min_id <= page_id <= max_id:
            return search_dir
        else:
            min_id = max_id
    return next(iter(dir_info))     # if not found, retuen the first value(AA)
 

In [6]:
# If nothing is found with search_dir, search again from the beginning
# this can be replaced by "get_files"
def get_all_files(base_path, search_dir):
    dir_iter = iter(dir_info.keys())   # in case search_dir fails
    dir_list = list(dir_info.keys())   # list of key
    cnt = 1
    while True:
        search_dir_path = os.path.join(base_path, search_dir)
        print(search_dir_path)
        for _, _, files in os.walk(search_dir_path):
            for file in files:
                yield os.path.join(search_dir_path, file)
        search_dir = next(dir_iter)
        cnt += 1
        if search_dir == dir_list[-1] and cnt == len(dir_list):
            # when nothing found
            return

In [7]:
# 
def get_files(base_path, search_dir):
    while True:
        search_dir_path = os.path.join(base_path, search_dir)
        print(search_dir_path)
        for _, _, files in os.walk(search_dir_path):
            for file in files:
                yield os.path.join(search_dir_path, file)
        else:
            return

In [8]:
# return each article text
def format_text(data):
    head = head_reg.search(data)  # (<doc id=...>)
    id_tag = id_reg.search(head.group())
    doc_id = re.search(r'\d+', id_tag.group())  # extract id from header
    title_tag = title_reg.search(head.group())
    doc_title = re.search(r'".+"', title_tag.group())  
    doc_id = int(doc_id.group())
    title = doc_title.group().replace('"', '')      # delete ""
    # deete each header(<doc id=...>)and tag
    # extract only texts (delete title as some articles have duplicated tittles)
    text = data.replace(head.group(), '').rstrip('</doc>')[len(title):]
    return doc_id, title, text

In [9]:
# return lists of articles
def get_articlelist(f_path):
    f = open(f_path, 'r', encoding='utf-8')
    file_data = f.read()
    file_data = file_data.replace('\n', '')
    return doc_reg.findall(file_data)

In [10]:
def output_file(f_name, text):
    # delete special characters which can't be used for file names
    f_name = re.sub(r'¥|/|:|\*|\?|"|<|>|\||', '', f_name)
    path = OUTPUT_PATH + f_name
    f = open(path, 'w', encoding='utf-8')
    f.write(text)
    f.close()

In [11]:
def output_file(f_name, text):
    # delete special characters which can't be used for file names
    f_name = re.sub(r'¥|/|:|\*|\?|"|<|>|\||', '', f_name)
    path = OUTPUT_PATH + f_name
    f = open(path, 'w', encoding='utf-8')
    f.write(text)
    f.close()

In [12]:
if __name__ == '__main__':
    # 
    id_reg = re.compile(r'id="\d+"')
    title_reg = re.compile(r'title=".+"')
    doc_reg = re.compile(r'<doc id=.+?</doc>')
    head_reg = re.compile(r'<doc id.+?">')

In [13]:
# NEED TO CHANGE for differendt data
BASE_PATH = 'F:/Wikipedia/wikiextractor-master/wikiextractor'
CSV_FILE = BASE_PATH + '/m_scientist.csv' # downloaded data from PetScan
WIKI_DIR = BASE_PATH + '/text'
OUTPUT_PATH = 'F:/Wikipedia/wikiextractor-master/wikiextractor/m_scientist/'

In [14]:
# make dictionary of the max ID value in each folder
dir_info = OrderedDict()
dir_info = mapping_dir(WIKI_DIR)
counter = 1     # loop counter

In [15]:
# read csv
f = open(CSV_FILE, 'r', encoding='utf-8')
reader = csv.reader(f)
next(csv.reader(f))

['number', 'title', 'pageid', 'namespace', 'length', 'touched']

In [16]:
not_found = {}      # dict for not-found data

In [17]:
# measure time
start_time = time.time()

In [18]:
for line in reader:
        flag = False
        page_name = line[1]
        page_id = int(line[2])
        namespace = line[3]
        if namespace == "Category" or namespace == "Template":
            continue
        search_dir = get_search_dir(page_id, dir_info)
        for f_path in get_files(WIKI_DIR, search_dir):
            for d in get_articlelist(f_path):
                doc_id, title, text = format_text(d)
                if page_id == doc_id:
                    print(counter, title)
                    output_file(title, text)
                    counter += 1
                    flag = True
                    break
            if flag:
                break
        else:
            not_found[page_id] = page_name
            print("ページID: {}は見つかりませんでした.".format(page_id))
 
        end_time = time.time()
        processing_time = end_time - start_time
        print('processing_time(sec): ', processing_time)
 
        # print "not found" page and its ID
        for i, (_id, _title) in enumerate(not_found.items()):
            print(i, _id, _title)

F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
1 手塚治虫
processing_time(sec):  1.3329999446868896
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
2 ドナルド・クヌース
processing_time(sec):  1.3921544551849365
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
3 マービン・ミンスキー
processing_time(sec):  1.4400694370269775
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
4 ノーム・チョムスキー
processing_time(sec):  1.5275046825408936
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
5 エドガー・ダイクストラ
processing_time(sec):  1.5845770835876465
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
6 リチャード・ストールマン
processing_time(sec):  1.6519713401794434
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
7 シャルル・メシエ
processing_time(sec):  1.72957444190979
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
8 老子
processing_time(sec):  1.8079864978790283
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
9 小柴昌俊
processing_time(sec):  1.9063565731048584
F:/Wikipedia/wikiextrac

75 ジョゼフ＝ルイ・ラグランジュ
processing_time(sec):  27.488523244857788
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
76 ルイ・ド・ブロイ
processing_time(sec):  28.088685512542725
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
77 エルヴィン・シュレーディンガー
processing_time(sec):  28.638070821762085
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
78 ニールス・ボーア
processing_time(sec):  29.175535678863525
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
79 福岡正信
processing_time(sec):  29.72389841079712
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
80 イリヤ・プリゴジン
processing_time(sec):  30.255946159362793
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
81 ローラン・シュヴァルツ
processing_time(sec):  30.825599670410156
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
82 カール・ワイエルシュトラス
processing_time(sec):  31.395076513290405
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AA
83 エウクレイデス
processing_time(sec):  31.93606662750244
F:/Wikipedia/wikiextractor-master/wikiextractor/tex

150 バートランド・ラッセル
processing_time(sec):  69.46855568885803
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
151 タルコット・パーソンズ
processing_time(sec):  69.84925127029419
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
152 諸橋轍次
processing_time(sec):  70.228355884552
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
153 ジャン・ル・ロン・ダランベール
processing_time(sec):  70.5993173122406
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
154 ポール・ディラック
processing_time(sec):  70.97192811965942
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
155 アレクサンダー・グラハム・ベル
processing_time(sec):  71.40932583808899
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
156 グリエルモ・マルコーニ
processing_time(sec):  71.87433123588562
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
157 サミュエル・P・ハンティントン
processing_time(sec):  72.36765599250793
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
158 クライド・トンボー
processing_time(sec):  72.87445211410522
F:/Wikipedia/wikiextractor-master/wikiext

224 ロバート・フック
processing_time(sec):  122.23863959312439
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
225 アントニ・ファン・レーウェンフック
processing_time(sec):  123.23700857162476
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
226 ウジェーヌ・デュボワ
processing_time(sec):  124.24000692367554
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
227 ロバート・ソロー
processing_time(sec):  125.23135209083557
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
228 グスタフ・キルヒホフ
processing_time(sec):  126.25176429748535
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AB
229 フーゴー・ユンカース
processing_time(sec):  127.2888662815094
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
230 パラケルスス
processing_time(sec):  127.39603781700134
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
231 栗本慎一郎
processing_time(sec):  127.48348951339722
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
232 リヒャルト・デーデキント
processing_time(sec):  127.56526732444763
F:/Wikipedia/wikiextractor-master/wikiextrac

298 上杉慎吉
processing_time(sec):  149.15611958503723
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
299 長谷川正安
processing_time(sec):  149.6568248271942
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
300 クルト・タンク
processing_time(sec):  150.17164587974548
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
301 ピエール・ルジャンドル
processing_time(sec):  150.67384266853333
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
302 ジョゼフ・バンクス・ライン
processing_time(sec):  151.19422554969788
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
303 萱野茂
processing_time(sec):  151.74661207199097
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
304 ライナス・ポーリング
processing_time(sec):  152.28309273719788
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
305 藤田哲也 (気象学者)
processing_time(sec):  152.88406705856323
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
306 中沢新一
processing_time(sec):  153.47349190711975
F:/Wikipedia/wikiextractor-master/wikiextractor/text\AC
307 高柳

...

ページID: 4614261は見つかりませんでした.
processing_time(sec):  19188.157487154007
0 3495952 ドノヴァン・コレル
1 4603612 井上剛_(人間工学者)
2 4604130 井口泰泉
3 4604153 田村類
4 4604426 鎌倉良成
5 4604629 宮道悦男
6 4604664 新宮清志
7 4604842 大平昌彦
8 4604950 岡野裕元
9 4605441 田原虎次
10 4605708 矢野眞和
11 4605909 エドワード・L・デシ
12 4606039 横山広充
13 4606115 菅沼拓夫
14 4606218 小森健吉
15 4606791 横山伸也
16 4606795 竹内義彰
17 4606924 柿崎明人
18 4607104 西口彰夫
19 4607156 吉岡剛_(教育学者)
20 4607261 松橋達矢
21 4607266 久保野茂
22 4607284 井上丹
23 4607291 糸長浩司
24 4607345 金本龍平
25 4607395 山口豊_(医学者)
26 4607401 ニール・ポストマン
27 4608459 ロバート・A・フロシュ
28 4608466 アラン・ラブレース
29 4608477 ダニエル・C・ドラッカー
30 4608482 アラン・ニードルマン
31 4608485 ウィリアム・プラーガー
32 4609067 角山剛
33 4609140 植木幸明
34 4609574 高野陽
35 4609810 清水雅彦_(憲法学者)
36 4610000 熊木俊朗
37 4610010 深田英朗
38 4610263 ロバート・シーマンズ・ジュニア
39 4610267 ウィリアム・ロバート・グラハム
40 4610421 鵜飼貞二
41 4610477 猪飼道夫
42 4610579 金子保_(教育学者)
43 4610863 長岡文雄
44 4611042 高津忠夫
45 4611157 石河利寛
46 4611208 クラレンス・バーズアイ
47 4611377 木村三生夫
48 4611504 霜田光一
49 4611511 松田岩男
50 4611522 郡司篤晃
51 4611587 松﨑典弥
52 

ページID: 4615350は見つかりませんでした.
processing_time(sec):  19194.871885061264
0 3495952 ドノヴァン・コレル
1 4603612 井上剛_(人間工学者)
2 4604130 井口泰泉
3 4604153 田村類
4 4604426 鎌倉良成
5 4604629 宮道悦男
6 4604664 新宮清志
7 4604842 大平昌彦
8 4604950 岡野裕元
9 4605441 田原虎次
10 4605708 矢野眞和
11 4605909 エドワード・L・デシ
12 4606039 横山広充
13 4606115 菅沼拓夫
14 4606218 小森健吉
15 4606791 横山伸也
16 4606795 竹内義彰
17 4606924 柿崎明人
18 4607104 西口彰夫
19 4607156 吉岡剛_(教育学者)
20 4607261 松橋達矢
21 4607266 久保野茂
22 4607284 井上丹
23 4607291 糸長浩司
24 4607345 金本龍平
25 4607395 山口豊_(医学者)
26 4607401 ニール・ポストマン
27 4608459 ロバート・A・フロシュ
28 4608466 アラン・ラブレース
29 4608477 ダニエル・C・ドラッカー
30 4608482 アラン・ニードルマン
31 4608485 ウィリアム・プラーガー
32 4609067 角山剛
33 4609140 植木幸明
34 4609574 高野陽
35 4609810 清水雅彦_(憲法学者)
36 4610000 熊木俊朗
37 4610010 深田英朗
38 4610263 ロバート・シーマンズ・ジュニア
39 4610267 ウィリアム・ロバート・グラハム
40 4610421 鵜飼貞二
41 4610477 猪飼道夫
42 4610579 金子保_(教育学者)
43 4610863 長岡文雄
44 4611042 高津忠夫
45 4611157 石河利寛
46 4611208 クラレンス・バーズアイ
47 4611377 木村三生夫
48 4611504 霜田光一
49 4611511 松田岩男
50 4611522 郡司篤晃
51 4611587 松﨑典弥
52 

ページID: 4616947は見つかりませんでした.
processing_time(sec):  19200.57978129387
0 3495952 ドノヴァン・コレル
1 4603612 井上剛_(人間工学者)
2 4604130 井口泰泉
3 4604153 田村類
4 4604426 鎌倉良成
5 4604629 宮道悦男
6 4604664 新宮清志
7 4604842 大平昌彦
8 4604950 岡野裕元
9 4605441 田原虎次
10 4605708 矢野眞和
11 4605909 エドワード・L・デシ
12 4606039 横山広充
13 4606115 菅沼拓夫
14 4606218 小森健吉
15 4606791 横山伸也
16 4606795 竹内義彰
17 4606924 柿崎明人
18 4607104 西口彰夫
19 4607156 吉岡剛_(教育学者)
20 4607261 松橋達矢
21 4607266 久保野茂
22 4607284 井上丹
23 4607291 糸長浩司
24 4607345 金本龍平
25 4607395 山口豊_(医学者)
26 4607401 ニール・ポストマン
27 4608459 ロバート・A・フロシュ
28 4608466 アラン・ラブレース
29 4608477 ダニエル・C・ドラッカー
30 4608482 アラン・ニードルマン
31 4608485 ウィリアム・プラーガー
32 4609067 角山剛
33 4609140 植木幸明
34 4609574 高野陽
35 4609810 清水雅彦_(憲法学者)
36 4610000 熊木俊朗
37 4610010 深田英朗
38 4610263 ロバート・シーマンズ・ジュニア
39 4610267 ウィリアム・ロバート・グラハム
40 4610421 鵜飼貞二
41 4610477 猪飼道夫
42 4610579 金子保_(教育学者)
43 4610863 長岡文雄
44 4611042 高津忠夫
45 4611157 石河利寛
46 4611208 クラレンス・バーズアイ
47 4611377 木村三生夫
48 4611504 霜田光一
49 4611511 松田岩男
50 4611522 郡司篤晃
51 4611587 松﨑典弥
52 4

ページID: 4617789は見つかりませんでした.
processing_time(sec):  19206.30895256996
0 3495952 ドノヴァン・コレル
1 4603612 井上剛_(人間工学者)
2 4604130 井口泰泉
3 4604153 田村類
4 4604426 鎌倉良成
5 4604629 宮道悦男
6 4604664 新宮清志
7 4604842 大平昌彦
8 4604950 岡野裕元
9 4605441 田原虎次
10 4605708 矢野眞和
11 4605909 エドワード・L・デシ
12 4606039 横山広充
13 4606115 菅沼拓夫
14 4606218 小森健吉
15 4606791 横山伸也
16 4606795 竹内義彰
17 4606924 柿崎明人
18 4607104 西口彰夫
19 4607156 吉岡剛_(教育学者)
20 4607261 松橋達矢
21 4607266 久保野茂
22 4607284 井上丹
23 4607291 糸長浩司
24 4607345 金本龍平
25 4607395 山口豊_(医学者)
26 4607401 ニール・ポストマン
27 4608459 ロバート・A・フロシュ
28 4608466 アラン・ラブレース
29 4608477 ダニエル・C・ドラッカー
30 4608482 アラン・ニードルマン
31 4608485 ウィリアム・プラーガー
32 4609067 角山剛
33 4609140 植木幸明
34 4609574 高野陽
35 4609810 清水雅彦_(憲法学者)
36 4610000 熊木俊朗
37 4610010 深田英朗
38 4610263 ロバート・シーマンズ・ジュニア
39 4610267 ウィリアム・ロバート・グラハム
40 4610421 鵜飼貞二
41 4610477 猪飼道夫
42 4610579 金子保_(教育学者)
43 4610863 長岡文雄
44 4611042 高津忠夫
45 4611157 石河利寛
46 4611208 クラレンス・バーズアイ
47 4611377 木村三生夫
48 4611504 霜田光一
49 4611511 松田岩男
50 4611522 郡司篤晃
51 4611587 松﨑典弥
52 4

ページID: 4619363は見つかりませんでした.
processing_time(sec):  19212.035511016846
0 3495952 ドノヴァン・コレル
1 4603612 井上剛_(人間工学者)
2 4604130 井口泰泉
3 4604153 田村類
4 4604426 鎌倉良成
5 4604629 宮道悦男
6 4604664 新宮清志
7 4604842 大平昌彦
8 4604950 岡野裕元
9 4605441 田原虎次
10 4605708 矢野眞和
11 4605909 エドワード・L・デシ
12 4606039 横山広充
13 4606115 菅沼拓夫
14 4606218 小森健吉
15 4606791 横山伸也
16 4606795 竹内義彰
17 4606924 柿崎明人
18 4607104 西口彰夫
19 4607156 吉岡剛_(教育学者)
20 4607261 松橋達矢
21 4607266 久保野茂
22 4607284 井上丹
23 4607291 糸長浩司
24 4607345 金本龍平
25 4607395 山口豊_(医学者)
26 4607401 ニール・ポストマン
27 4608459 ロバート・A・フロシュ
28 4608466 アラン・ラブレース
29 4608477 ダニエル・C・ドラッカー
30 4608482 アラン・ニードルマン
31 4608485 ウィリアム・プラーガー
32 4609067 角山剛
33 4609140 植木幸明
34 4609574 高野陽
35 4609810 清水雅彦_(憲法学者)
36 4610000 熊木俊朗
37 4610010 深田英朗
38 4610263 ロバート・シーマンズ・ジュニア
39 4610267 ウィリアム・ロバート・グラハム
40 4610421 鵜飼貞二
41 4610477 猪飼道夫
42 4610579 金子保_(教育学者)
43 4610863 長岡文雄
44 4611042 高津忠夫
45 4611157 石河利寛
46 4611208 クラレンス・バーズアイ
47 4611377 木村三生夫
48 4611504 霜田光一
49 4611511 松田岩男
50 4611522 郡司篤晃
51 4611587 松﨑典弥
52 